# Installing Libraries

In [ ]:
!pip install -q scikit-learn==1.4.1.post1 numpy pandas plotly altair

이번 실습에서는 계속 써왔던 [altair](https://altair-viz.github.io/)와 더불어, 또 다른 유명한 Python 시각화 라이브러리인 [plotly](https://plotly.com/)를 써보도록 하자. altair 대신 plotly를 쓰는 특별한 이유는, plotly 쪽이 3D 그래프를 그리기 용이하기 때문이다.

# Data Preparation

In [ ]:
from sklearn.datasets import make_swiss_roll, load_digits
import pandas as pd


X_SR, COLOR_SR = make_swiss_roll(n_samples=1500, noise=0.2, random_state=42)
X_DIGITS, y_DIGITS = load_digits(as_frame=True, return_X_y=True)

이번 실습에서는 고차원의 복잡한 데이터를 해당 고차원을 잘 설명할 수 있는 저차원의 데이터Intrinsic Manifold로 바꾸는 게 목적이므로, 3차원의 비선형적인 데이터인 **swiss roll**과, 8X8 픽셀값(즉, 64차원)으로 구성된 **handwritten digit** 데이터를 활용해보겠다.

In [ ]:
import plotly.express as px

df = pd.DataFrame(X_SR, columns=['x', 'y', 'z']).assign(
    color=COLOR_SR
)

px.scatter_3d(
    df, x='x', y='y', z='z', color='color'
).update_traces(
    marker_size=2
).update_layout(
    margin=dict(t=0, b=0, l=0, r=0)
)

보다시피, **swiss roll**은 이름 그대로 롤빵 형식으로 3차원에 데이터가 분포되어 있다.

In [ ]:
X_DIGITS

pixel_0_0  pixel_0_1  pixel_0_2  pixel_0_3  pixel_0_4  pixel_0_5  \
0           0.0        0.0        5.0       13.0        9.0        1.0   
1           0.0        0.0        0.0       12.0       13.0        5.0   
2           0.0        0.0        0.0        4.0       15.0       12.0   
3           0.0        0.0        7.0       15.0       13.0        1.0   
4           0.0        0.0        0.0        1.0       11.0        0.0   
...         ...        ...        ...        ...        ...        ...   
1792        0.0        0.0        4.0       10.0       13.0        6.0   
1793        0.0        0.0        6.0       16.0       13.0       11.0   
1794        0.0        0.0        1.0       11.0       15.0        1.0   
1795        0.0        0.0        2.0       10.0        7.0        0.0   
1796        0.0        0.0       10.0       14.0        8.0        1.0   

      pixel_0_6  pixel_0_7  pixel_1_0  pixel_1_1  ...  pixel_6_6  pixel_6_7  \
0           0.0        0.0        0.0        0.0  ...        0.0        0.0   
1           0.0        0.0        0.0        0.0  ...        0.0        0.0   
2           0.0        0.0        0.0        0.0  ...        5.0        0.0   
3           0.0        0.0        0.0        8.0  ...        9.0        0.0   
4           0.0        0.0        0.0        0.0  ...        0.0        0.0   
...         ...        ...        ...        ...  ...        ...        ...   
1792        0.0        0.0        0.0        1.0  ...        4.0        0.0   
1793        1.0        0.0        0.0        0.0  ...        1.0        0.0   
1794        0.0        0.0        0.0        0.0  ...        0.0        0.0   
1795        0.0        0.0        0.0        0.0  ...        2.0        0.0   
1796        0.0        0.0        0.0        2.0  ...        8.0        0.0   

      pixel_7_0  pixel_7_1  pixel_7_2  pixel_7_3  pixel_7_4  pixel_7_5  \
0           0.0        0.0        6.0       13.0       10.0        0.0   
1           0.0        0.0        0.0       11.0       16.0       10.0   
2           0.0        0.0        0.0        3.0       11.0       16.0   
3           0.0        0.0        7.0       13.0       13.0        9.0   
4           0.0        0.0        0.0        2.0       16.0        4.0   
...         ...        ...        ...        ...        ...        ...   
1792        0.0        0.0        2.0       14.0       15.0        9.0   
1793        0.0        0.0        6.0       16.0       14.0        6.0   
1794        0.0        0.0        2.0        9.0       13.0        6.0   
1795        0.0        0.0        5.0       12.0       16.0       12.0   
1796        0.0        1.0        8.0       12.0       14.0       12.0   

      pixel_7_6  pixel_7_7  
0           0.0        0.0  
1           0.0        0.0  
2           9.0        0.0  
3           0.0        0.0  
4           0.0        0.0  
...         ...        ...  
1792        0.0        0.0  
1793        0.0        0.0  
1794        0.0        0.0  
1795        0.0        0.0  
1796        1.0        0.0  

[1797 rows x 64 columns]

**handwritten digit**데이터는 8X8 픽셀의 값으로 구성되어 있다.

# Principal Component Analysis
먼저, 주성분 분석부터 해보자.

## Vanilla PCA
기본적인 주성분 분석을 하는 것은 아주 간단하다. scikit-learn에서 [sklearn.decomposition.PCA](https://scikit-learn.org/stable/modules/generated/sklearn.decomposition.PCA.html#sklearn.decomposition.PCA) 클래스를 이용하면 된다.

In [ ]:
from sklearn.decomposition import PCA


pca = PCA(
    svd_solver='full' # 전체 샘플들로 공분산 행렬을 구해서 주성분을 계산한다. 다른 설정에 대해선 아래에서 설명한다.
).fit(X_SR)

기본적으로 샘플수 또는 특성값 차원수 중 작은 값 만큼의 주성분을 구한다. **swiss roll**은 3차원이므로, 3차원의 주성분을 계산한다.

각 주성분이 차지하는 분산의 비율은 다음과 같이 확인할 수 있다.

In [ ]:
pca.explained_variance_ratio_

array([0.40697979, 0.30641404, 0.28660618])

위에서 보듯, 첫 번째 주성분은 전체 분산의 40.7%, 두 번째는 30.6%, 세 번째는 28.9%를 설명할 수 있다.
사실, 이렇게 보는 것 보다는 누적합Cumulative Sum을 보는 게 더 낫다. 아래와 같이 해보자.

In [ ]:
import numpy as np


np.cumsum(pca.explained_variance_ratio_)

array([0.40697979, 0.71339382, 1.        ])

위처럼, 두 번째 주성분까지 취한다면 전체 분산의 71.3%를 설명할 수 있게 된다. 어렵게 생각할 필요 없이, 3차원 데이터를 2차원 데이터로 축소했을 때, 원본 데이터의 71.3% 정도를 반영할 수 있다고 이해하면 된다.

그럼, 과연 2차원으로 차원을 축소했을 때 어떻게 보여질까? 시각화해보자.

In [ ]:
from sklearn.decomposition import PCA
import pandas as pd
import altair as alt


proj = PCA(
    svd_solver='full',
    n_components=2 # 계산할 주성분 개수를 의미한다.
).fit_transform(X_SR)

df = pd.DataFrame(proj, columns=['PC1', 'PC2']).assign(
    color=COLOR_SR
)

alt.Chart(df).encode(
    x='PC1', y='PC2', color=alt.Color('color', scale=alt.Scale(scheme='inferno'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
)

alt.Chart(...)

흥미롭게도, 원본 데이터의 롤 형태의 모습은 그대로 유지된채로 2차원으로 변경된 것을 알 수 있다.

그럼, 64차원짜리 데이터인 **handwritten digits**을 2차원으로 줄인다면 어떻게 될까? 한번 시각화해보자.

In [ ]:
from sklearn.decomposition import PCA
import pandas as pd
import altair as alt


proj = PCA(
    svd_solver='full',
    n_components=2
).fit_transform(X_DIGITS)

df = pd.DataFrame(proj, columns=['PC1', 'PC2']).assign(
    label=y_DIGITS
)

alt.Chart(df).encode(
    x='PC1', y='PC2', color=alt.Color('label:N', scale=alt.Scale(scheme='category10'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
).interactive()

alt.Chart(...)

위에서 보다시피,  같은 숫자끼리는 어느 정도 한 곳에 모여있는듯한 경향을 보이지만, 구분되지 않은 숫자들도 중앙에 굉장히 많음을 알 수 있다(예. 숫자 5와 8)

In [ ]:
from sklearn.decomposition import PCA
import pandas as pd
import plotly.express as px


proj = PCA(
    svd_solver='full', n_components=3
).fit_transform(X_DIGITS)

df = pd.DataFrame(proj, columns=['PC1', 'PC2', 'PC3']).assign(
    label=y_DIGITS.astype(str)
)

px.scatter_3d(
    df, x='PC1', y='PC2', z='PC3', color='label'
).update_traces(
    marker_size=2
).update_layout(
    margin=dict(t=0, b=0, l=0, r=0)
)

주성분을 3개로 늘려도 여전히 5와 8은 잘 구분이 되지 않는다. 대체 몇 개의 주성분이 있어야 원본 데이터를 잘 반영할 수 있을까?

In [ ]:
from sklearn.decomposition import PCA
import pandas as pd
import numpy as np
import altair as alt


pca = PCA(
    svd_solver='full'
).fit(X_DIGITS)

var = pca.explained_variance_ratio_
df = pd.DataFrame(dict(x=np.arange(len(var)), y=np.cumsum(var)))
alt.Chart(df).encode(
    x=alt.X('x', title='PC Components'),
    y=alt.Y('y', title='Cum. sum of variance ratios')
).mark_line().properties(
    width=800, height=600,
).interactive()

alt.Chart(...)

가장 좋은 방법은, 주성분 갯수에 따라서 설명되는 누적 분산합을 확인해보는 것이다. 2개의 주성분으로는 40%, 3개의 주성분으로는 48% 정도였으니, 절반 이상의 분산은 설명이 여전히 되지 않았다. 대신, 27~28개 정도의 주성분이면 약 95% 정도의 분산을 설명할 수 있다. 64차원을 95% 정도의 정보를 유지한 채로 27차원으로 줄인다면 충분히 의미가 있는 축소라고 할 수 있을 것이다.

## Randomized PCA
이젠, 큰 데이터 셋에 대해 직접 주성분을 계산하기보다는 주성분을 근사하는 방법인 Randomized PCA를 써보자. 방법은 간단하다. 기본 PCA에서 **svd_solver**를 *'randomized'*로 바꿔주면 된다.

In [ ]:
from sklearn.decomposition import PCA
import pandas as pd
import altair as alt


proj = PCA(
    svd_solver='randomized',
    n_components=2
).fit_transform(X_DIGITS)

df = pd.DataFrame(proj, columns=['PC1', 'PC2']).assign(
    label=y_DIGITS.astype(str)
)

alt.Chart(df).encode(
    x='PC1', y='PC2', color=alt.Color('label:N', scale=alt.Scale(scheme='category10'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
).interactive()

alt.Chart(...)

언제 Randomized PCA를 활용해야할까? scikit-learn의 기본 설정에서는 차원 또는 샘플의 수 중 큰 값이 500보다 크고, 뽑고자 하는 주성분의 수가 차원 또는 샘플의 수 중 작은 값의 80% 미만이라면(예. 샘플 수 1000, 차원수 64이고 51개의 주성분을 추출하고자 함) Randomized PCA를 활용하는 것을 권장하고 있다. 즉, 데이터의 크기가 커서 행렬 연산의 양이 많아진다면 Randomized PCA를 활용하면 된다. 물론, 컴퓨터의 성능과 메모리가 충분히 좋다면 상관없다.

## Incremental PCA
Incremental PCA는 기본 PCA가 아니라, 별도의 구현체인 [sklearn.decomposition.IncrementalPCA](https://scikit-learn.org/stable/modules/generated/sklearn.decomposition.IncrementalPCA.html#sklearn.decomposition.IncrementalPCA)를 활용해야 한다.

In [ ]:
from sklearn.decomposition import IncrementalPCA
import pandas as pd
import altair as alt


proj = IncrementalPCA(
    n_components=2, # 계산할 주성분 개수를 의미한다.
    batch_size=15 # 미니 배치의 크기를 의미한다. 기본적으론 특성값 차원 수 X 5로 설정되어 있다.
).fit_transform(X_SR)

df = pd.DataFrame(proj, columns=['PC1', 'PC2']).assign(
    color=COLOR_SR
)

alt.Chart(df).encode(
    x='PC1', y='PC2', color=alt.Color('color', scale=alt.Scale(scheme='inferno'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
)

alt.Chart(...)

In [ ]:
from sklearn.decomposition import IncrementalPCA
import pandas as pd
import plotly.express as px


proj = IncrementalPCA(
    n_components=2,
    batch_size=None
).fit_transform(X_DIGITS)

df = pd.DataFrame(proj, columns=['PC1', 'PC2']).assign(
    label=y_DIGITS.astype(str)
)

alt.Chart(df).encode(
    x='PC1', y='PC2', color=alt.Color('label:N', scale=alt.Scale(scheme='category10'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
).interactive()

alt.Chart(...)

## Kernel PCA
이번엔 Kernel Trick을 활용하는 PCA를 활용해보자. [sklearn.decomposition.KernelPCA](https://scikit-learn.org/stable/modules/generated/sklearn.decomposition.KernelPCA.html#sklearn.decomposition.KernelPCA)를 사용하면 된다.

In [ ]:
from sklearn.decomposition import KernelPCA
import pandas as pd
import altair as alt


proj = KernelPCA(
    n_components=2, # 계산할 주성분 개수를 의미한다.
    kernel='rbf' # Radial Basis Function Kernel를 활용해보자.
).fit_transform(X_SR)

df = pd.DataFrame(proj, columns=['PC1', 'PC2']).assign(
    color=COLOR_SR
)

alt.Chart(df).encode(
    x='PC1', y='PC2', color=alt.Color('color', scale=alt.Scale(scheme='inferno'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
)

alt.Chart(...)

In [ ]:
from sklearn.decomposition import KernelPCA
import pandas as pd
import plotly.express as px


proj = KernelPCA(
    n_components=2, # 계산할 주성분 개수를 의미한다.
    kernel='rbf' # Radial Basis Function Kernel를 활용해보자.
).fit_transform(X_DIGITS)

df = pd.DataFrame(proj, columns=['PC1', 'PC2']).assign(
    label=y_DIGITS.astype(str)
)

alt.Chart(df).encode(
    x='PC1', y='PC2', color=alt.Color('label:N', scale=alt.Scale(scheme='category10'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
).interactive()

alt.Chart(...)

# Random Projection
PCA는 이것으로 마무리하고, 이번엔 고차원의 데이터를 무작위로 저차원으로 투영하는 방법을 활용해보자.
문제는, 과연 몇 차원으로 투영해야 오차가 예상 범위내일까? 이를 위해서 [sklearn.random_projection.johnson_lindenstrauss_min_dim](https://scikit-learn.org/stable/modules/generated/sklearn.random_projection.johnson_lindenstrauss_min_dim.html#sklearn.random_projection.johnson_lindenstrauss_min_dim)를 실행하면 된다.

In [ ]:
from sklearn.random_projection import johnson_lindenstrauss_min_dim


johnson_lindenstrauss_min_dim(
    n_samples=len(X_SR), # 샘플 수
    eps=0.1 # 오차 허용율을 의미한다. 크면 클수록 투영된 데이터가 원본 데이터와 차이가 나게 된다.
)

6268

놀랍게도, 3차원 데이터를 0.1의 오차율로 투영하려면 무려 6,268이라는 차원이 필요하다. 물론, 어디까지나 이론적으로 그렇다는 것이고 실제로는 임의의 차원수로 투영할 수 있다.


## Gaussian Random Projection
Gaussian 분포를 따르는 무작위 투영은 [sklearn.random_projection.GaussianRandomProjection](https://scikit-learn.org/stable/modules/generated/sklearn.random_projection.GaussianRandomProjection.html#sklearn.random_projection.GaussianRandomProjection)를 활용한다.

In [ ]:
from sklearn.random_projection import GaussianRandomProjection
import pandas as pd
import altair as alt


proj = GaussianRandomProjection(
    n_components=2, # 투영할 차원수를 의미한다.
    random_state=42
).fit_transform(X_SR)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    color=COLOR_SR
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('color', scale=alt.Scale(scheme='inferno'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
)

alt.Chart(...)

In [ ]:
from sklearn.random_projection import GaussianRandomProjection
import pandas as pd
import plotly.express as px


proj = GaussianRandomProjection(
    n_components=2, # 투영할 차원수를 의미한다.
    random_state=42
).fit_transform(X_DIGITS)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    label=y_DIGITS
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('label:N', scale=alt.Scale(scheme='category10'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
).interactive()

alt.Chart(...)

## Sparse Random Projection

 희소 무작위 투영은 [sklearn.random_projection.SparseRandomProjection](https://scikit-learn.org/stable/modules/generated/sklearn.random_projection.SparseRandomProjection.html#sklearn.random_projection.SparseRandomProjection)을 활용하면 된다.

In [ ]:
from sklearn.random_projection import SparseRandomProjection
import pandas as pd
import numpy as np
import altair as alt


proj = SparseRandomProjection(
    n_components=2, # 투영할 차원수를 의미한다.
    density=1 / np.sqrt(X_SR.shape[1]), # 초매개변수 "s"를 의미한다.
    random_state=42
).fit_transform(X_SR)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    color=COLOR_SR
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('color', scale=alt.Scale(scheme='inferno'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
)

alt.Chart(...)

In [ ]:
from sklearn.random_projection import SparseRandomProjection
import pandas as pd
import numpy as np
import altair as alt


proj = SparseRandomProjection(
    n_components=2, # 투영할 차원수를 의미한다.
    density=1 / np.sqrt(X_DIGITS.shape[1]), # 초매개변수 "s"를 의미한다.
    random_state=42
).fit_transform(X_DIGITS)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    label=y_DIGITS.astype('str')
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('label:N', scale=alt.Scale(scheme='category10'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
).interactive()

alt.Chart(...)

# Multidimensional Scaling
이번엔 고차원의 샘플쌍 간의 거리를 최대한 유지하려고 하는 Multidimensional Scaling을 활용해보자. [sklearn.manifold.MDS](https://scikit-learn.org/stable/modules/generated/sklearn.manifold.MDS.html#sklearn.manifold.MDS)에 구현되어 있다.

In [ ]:
from sklearn.manifold import MDS
import pandas as pd
import altair as alt


proj = MDS(
    n_components=2, # 투영할 차원수를 의미한다.
    metric=True, # 샘플쌍간의 정확한 거리(Euclidean distance)를 활용한다.
    random_state=42
).fit_transform(X_SR)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    color=COLOR_SR
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('color', scale=alt.Scale(scheme='inferno'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
)

alt.Chart(...)

In [ ]:
from sklearn.manifold import MDS
import pandas as pd
import altair as alt


proj = MDS(
    n_components=2, # 투영할 차원수를 의미한다.
    metric=False, # 정확한 거리 값 대신에 데이터를 오름차순으로 정렬한 후 그 순서Rank를 기반으로 거리를 계산한다.
    random_state=42
).fit_transform(X_DIGITS)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    label=y_DIGITS
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('label:N', scale=alt.Scale(scheme='category10'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
).interactive()

alt.Chart(...)

# Isometric Mapping
이번엔 MDS와 유사하나, 인접한 샘플들을 활용해서 거리를 측정하는 Isomap을 써보자. [sklearn.manifold.Isomap](https://scikit-learn.org/stable/modules/generated/sklearn.manifold.Isomap.html#sklearn.manifold.Isomap)을 활용하면 된다.

In [ ]:
from sklearn.manifold import Isomap
import pandas as pd
import altair as alt


proj = Isomap(
    n_components=2, # 투영할 차원수를 의미한다.
    n_neighbors=30, # 인접한 샘플의 수를 의미한다.
).fit_transform(X_SR)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    color=COLOR_SR
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('color', scale=alt.Scale(scheme='inferno'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
)

alt.Chart(...)

In [ ]:
from sklearn.manifold import Isomap
import pandas as pd
import altair as alt


proj = Isomap(
    n_components=2, # 투영할 차원수를 의미한다.
    n_neighbors=30, # 인접한 샘플의 수를 의미한다.
).fit_transform(X_DIGITS)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    label=y_DIGITS
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('label:N', scale=alt.Scale(scheme='category10'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
).interactive()

alt.Chart(...)

# Locally Linear Embedding
이번엔 MDS와 유사하나, 거리 대신 가중치를 활용하는 LLE를 써보자. [sklearn.manifold.LocallyLinearEmbedding](https://scikit-learn.org/stable/modules/generated/sklearn.manifold.LocallyLinearEmbedding.html#sklearn.manifold.LocallyLinearEmbedding)를 사용하면 된다.

## Vanilla LLE

In [ ]:
from sklearn.manifold import LocallyLinearEmbedding
import pandas as pd
import altair as alt


proj = LocallyLinearEmbedding(
    n_components=2, # 투영할 차원수를 의미한다.
    n_neighbors=30, # 인접한 샘플의 수를 의미한다.
    method='standard' # 기본 LLE를 의미한다.
).fit_transform(X_SR)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    color=COLOR_SR
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('color', scale=alt.Scale(scheme='inferno'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
)

alt.Chart(...)

In [ ]:
from sklearn.manifold import LocallyLinearEmbedding
import pandas as pd
import altair as alt


proj = LocallyLinearEmbedding(
    n_components=2, # 투영할 차원수를 의미한다.
    n_neighbors=30, # 인접한 샘플의 수를 의미한다.
    method='standard' # 기본 LLE를 의미한다.
).fit_transform(X_DIGITS)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    label=y_DIGITS
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('label:N', scale=alt.Scale(scheme='category10'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
).interactive()

alt.Chart(...)

## Modified LLE

In [ ]:
from sklearn.manifold import LocallyLinearEmbedding
import pandas as pd
import altair as alt


proj = LocallyLinearEmbedding(
    n_components=2, # 투영할 차원수를 의미한다.
    n_neighbors=30, # 인접한 샘플의 수를 의미한다.
    method='modified' # Modified LLE를 의미한다.
).fit_transform(X_SR)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    color=COLOR_SR
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('color', scale=alt.Scale(scheme='inferno'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
)

alt.Chart(...)

In [ ]:
from sklearn.manifold import LocallyLinearEmbedding
import pandas as pd
import altair as alt


proj = LocallyLinearEmbedding(
    n_components=2, # 투영할 차원수를 의미한다.
    n_neighbors=30, # 인접한 샘플의 수를 의미한다.
    method='modified' # Modified LLE를 의미한다.
).fit_transform(X_DIGITS)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    label=y_DIGITS
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('label:N', scale=alt.Scale(scheme='category10'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
).interactive()

alt.Chart(...)

## Hessian LLE

In [ ]:
from sklearn.manifold import LocallyLinearEmbedding
import pandas as pd
import altair as alt


proj = LocallyLinearEmbedding(
    n_components=2, # 투영할 차원수를 의미한다.
    n_neighbors=30, # 인접한 샘플의 수를 의미한다.
    method='hessian', # Hessian LLE를 의미한다.,
).fit_transform(X_SR)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    color=COLOR_SR
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('color', scale=alt.Scale(scheme='inferno'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
)

alt.Chart(...)

In [ ]:
from sklearn.manifold import LocallyLinearEmbedding
import pandas as pd
import altair as alt


proj = LocallyLinearEmbedding(
    n_components=2, # 투영할 차원수를 의미한다.
    n_neighbors=30, # 인접한 샘플의 수를 의미한다.
    method='hessian', # Hessian LLE를 의미한다.
).fit_transform(X_DIGITS)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    label=y_DIGITS
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('label:N', scale=alt.Scale(scheme='category10'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
).interactive()

alt.Chart(...)

# Spectral Embedding
이번엔 Laplacian Graph를 활용하는 Spectral Embedding이다. [sklearn.manifold.SpectralEmbedding](https://scikit-learn.org/stable/modules/generated/sklearn.manifold.SpectralEmbedding.html#sklearn.manifold.SpectralEmbedding)으로 사용할 수 있다.

In [ ]:
from sklearn.manifold import SpectralEmbedding
import pandas as pd
import altair as alt


proj = SpectralEmbedding(
    n_components=2, # 투영할 차원수를 의미한다.
    n_neighbors=30, # 인접한 샘플의 수를 의미한다.
).fit_transform(X_SR)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    color=COLOR_SR
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('color', scale=alt.Scale(scheme='inferno'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
)

alt.Chart(...)

In [ ]:
from sklearn.manifold import SpectralEmbedding
import pandas as pd
import altair as alt


proj = SpectralEmbedding(
    n_components=2, # 투영할 차원수를 의미한다.
    n_neighbors=30, # 인접한 샘플의 수를 의미한다.
).fit_transform(X_DIGITS)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    label=y_DIGITS
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('label:N', scale=alt.Scale(scheme='category10'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
).interactive()

alt.Chart(...)

# t-Distributed Stochastic Neighbor Embedding
마지막으로는 고차원 데이터를 저차원에서 적절히 시각화하기 위한 t-SNE를 활용해보자. [sklearn.manifold.TSNE](https://scikit-learn.org/stable/modules/generated/sklearn.manifold.TSNE.html#sklearn.manifold.TSNE)를 지금까지 했던 것처럼 활용하면 된다.


In [ ]:
from sklearn.manifold import TSNE
import pandas as pd
import altair as alt


proj = TSNE(
    n_components=2, # 투영할 차원수를 의미한다.
    perplexity=30, # 인접한 샘플의 수를 의미한다.
    random_state=42
).fit_transform(X_SR)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    color=COLOR_SR
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('color', scale=alt.Scale(scheme='inferno'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
)

alt.Chart(...)

In [ ]:
from sklearn.manifold import TSNE
import pandas as pd
import altair as alt


proj = TSNE(
    n_components=2, # 투영할 차원수를 의미한다.
    perplexity=30, # 인접한 샘플의 수를 의미한다.
    random_state=42
).fit_transform(X_DIGITS)

df = pd.DataFrame(proj, columns=['D1', 'D2']).assign(
    label=y_DIGITS
)

alt.Chart(df).encode(
    x='D1', y='D2', color=alt.Color('label:N', scale=alt.Scale(scheme='category10'))
).mark_point(filled=True, opacity=0.8).properties(
    width=600, height=400
).interactive()

alt.Chart(...)

# All-in-One Comparisons
지금까지 했던 모든 방법들을 한번에 비교해보자.


In [ ]:
from sklearn.decomposition import PCA, IncrementalPCA, KernelPCA
from sklearn.random_projection import GaussianRandomProjection, SparseRandomProjection
from sklearn.manifold import MDS, Isomap, LocallyLinearEmbedding, SpectralEmbedding, TSNE


METHODS = {
    'Vanilla PCA': PCA(n_components=2, svd_solver='full'),
    'Randomized PCA': PCA(n_components=2, svd_solver='randomized', random_state=42),
    'Incremental PCA': IncrementalPCA(n_components=2),
    'RBF-Kernel PCA': KernelPCA(n_components=2, kernel='rbf'),
    'Polynomial-Kernel PCA': KernelPCA(n_components=2, kernel='poly'),
    'Gaussian RP': GaussianRandomProjection(n_components=2, random_state=42),
    'Sparse RP': SparseRandomProjection(n_components=2, random_state=42),
    'Metric MDS': MDS(n_components=2, metric=True, random_state=42),
    'Non-metric MDS': MDS(n_components=2, metric=False, random_state=42),
    'Isomap': Isomap(n_components=2, n_neighbors=30),
    'Vanilla LLE': LocallyLinearEmbedding(n_components=2, n_neighbors=30, method='standard'),
    'Modified LLE': LocallyLinearEmbedding(n_components=2, n_neighbors=30, method='modified'),
    'Hessian LLE': LocallyLinearEmbedding(n_components=2, n_neighbors=30, method='hessian'),
    'Spectral Embedding': SpectralEmbedding(n_components=2, n_neighbors=30),
    't-SNE': TSNE(n_components=2, perplexity=30, random_state=42)
}


## Swiss Roll

In [ ]:
import pandas as pd
import altair as alt


CHARTS_SR = []

for name, func in METHODS.items():
    proj = func.fit_transform(X_SR)
    df = pd.DataFrame(
        proj, columns=['D1', 'D2']
    ).assign(
        color=COLOR_SR,
    )
    chart = alt.Chart(df).encode(
        x='D1', y='D2', color=alt.Color('color', scale=alt.Scale(scheme='inferno'))
    ).mark_point(filled=True, opacity=0.8).properties(
        width=200, height=200
    ).properties(
        title=name
    )
    CHARTS_SR.append(chart)

In [ ]:
import altair as alt


chart_rows = [alt.hconcat(*CHARTS_SR[i:i+4]) for i in range(0, len(CHARTS_SR), 4)]
alt.vconcat(*chart_rows)

alt.VConcatChart(...)

## Handwritten Digits

In [ ]:
import pandas as pd
import altair as alt


CHARTS_DIGITS = []

for name, func in METHODS.items():
    proj = func.fit_transform(X_DIGITS)
    df = pd.DataFrame(
        proj, columns=['D1', 'D2']
    ).assign(
        label=y_DIGITS,
    )
    chart = alt.Chart(df).encode(
        x='D1', y='D2', color=alt.Color('label:N', scale=alt.Scale(scheme='category10'))
    ).mark_point(filled=True, opacity=0.8).properties(
        width=200, height=200
    ).properties(
        title=name
    )
    CHARTS_DIGITS.append(chart)

In [ ]:
import altair as alt


chart_rows = [alt.hconcat(*CHARTS_DIGITS[i:i+4]) for i in range(0, len(CHARTS_DIGITS), 4)]
alt.vconcat(*chart_rows)

alt.VConcatChart(...)